Previously, we had created invidual masked regions from sattellite images and
shapefiles of our blockgroups. Now we will further sample some number of square
images from each blockgroup to create the training input to our classifier. Each
square block will contain 4 layers of image data in the RGBA band which we will
flatten into a 1-D array and pickle within a folder structure whose name is the

GEOID region from which the image was sampled.

In [1]:
import helper
import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np
import os
from PIL import Image
import pickle

In [2]:
def initialize_folder(filename):
    '''Given a filename, will create ./data/{filename} folder
    
    Args:
        filename (str): String of filename which will be used to create folder name
    
    Returns:
        None - Creates folder under ./data/
    '''
       
    if not os.path.exists(f'./data/samples/{filename}'):
        os.makedirs(f'./data/samples/{filename}')

In [3]:
# Test with 1 image
def sample_bagging(im_fp, out_name, box_dim, black_thres = .15, bag_size=20,
                   resize_ratio=.7, exclude_NIR=False, greyscale=True):
    '''In order to create a data set from each geospatial blockgroup, we
    will employ a bagging method and pick a bounding box to crop a sample from.
    We will do this with replacement (which should help our algorithm with)
    spatial invariance.
    
    Args:
        im_fp (str): Path to image
        out_name (str): Name of output sample images (folder structures will be
        initialized under ./data/{out_name}/). Will have pkl appended in output.
        box_dim (int): Pixel number for both dims of square crop box
        black_thres (float): Ratio between 0-1 dictacting tolerance for black pixels.
            This is so we don't just sample black pixels which is the masking.
        bag_size (int): How many samples we will draw from our image
        resize_ratio (float): A number between 0-1 multiplying our original image dimensions
            in order to resize to a smaller dim.
        exclude_NIR (bool): In case we need to get rid of even more data, set to true
            so we only use RGB bands (reducing pixels by 1/4)
        
    Returns:
        None - outputs pickle files that can later be loaded
    '''
    # Create folder for samples if it doesn't already exist
    initialize_folder(out_name)
    
    # Open image and resize
    im = Image.open(im_fp)
    og_size = im.size
    new_size = np.multiply(list(im.size), resize_ratio)
    new_size = np.round(new_size).astype(int)
    im = im.resize(new_size, Image.ANTIALIAS)
    
    # Print status for diagnostics
    capacity = new_size[0]*new_size[1]/box_dim**2
    print(f'Resized area is {new_size} pixels (from),', og_size)
    print(f'Can sample ~{capacity} unique images')
    
    # Loop through randomly sampled squares, only accepting
    # samples with less than defined threshold of black pixels
    samples = 0
    while samples < bag_size:
        # Pick random integer in range of our dims - box_dim,
        # will be coordinate of top left corner of our mask
        rand_y = np.random.randint(0, new_size[0]-box_dim)
        rand_x = np.random.randint(0, new_size[1]-box_dim)
        x0, x1 = rand_x, rand_x + box_dim
        y0, y1 = rand_y, rand_y + box_dim
        
        # Crop (left, top, right, bottom)
        im_cropped = im.crop((x0, y0, x1, y1))
        im_arr = np.array(im_cropped)
    
        # Count number of black pixels through all 4 bands
        black = 0
        for pixel in im_cropped.getdata():
            if pixel == (0, 0, 0, 0): # if your image is RGB (if RGBA, (0, 0, 0, 255) or so
                black += 1
        black_ratio = black/(mask_size**2)

        # In case we want to reduce data/pixels by 1/3, we can exclude
        # near infrared band
        if exclude_NIR:
            im_arr = im_arr[:,:,:3]
            
        if greyscale:
            # Luminance preserving transformation: Y' = 0.299 R + 0.587 G + 0.114 B 
            im_arr = np.dot(im_arr[...,:3], [0.299, 0.587, 0.114])
        
        if black_ratio > black_thres:
            print(f'Black ratio: {black_ratio}, skipping...')
            continue
        else:
            # Append sample number and .pkl to out_name ending
            out_file = out_name + '_' + (str(samples+1)) + '.pkl'
            print(f'Black ratio: {black_ratio}, writing to {out_file}')
            
            # Normalize RGBA values to between 0-1
            im_arr = im_arr.flatten()
            im_arr = np.divide(im_arr, 255)
            pickle.dump(im_arr, open(f'./data/samples/{out_name}/{out_file}', "wb" ) )
            samples +=1
            
    

In [6]:
data_path = './data/blockgroup_income_merged.shp'
sf_income_blockgroup = helper.load_shapefile(data_path)

block_area = sf_income_blockgroup['GEOID'].values
threshold = .31
target = [0 if x <= threshold else 1 for x in sf_income_blockgroup['25k_ratio'].values]
low_income_ratio = sum(target)/len(target)
high_income_ratio = 1-low_income_ratio

counter = 0
for neighborhood_class, out_name in zip(target, block_area):
    # Since lower income class is minority class in most threshold values,
    # We will sample it more often to create ~50-50 balance
    bag_size = 40
#     if not neighborhood_class:
#         # This will yield us approximately equal classes based on threshold
#         bag_size = int(low_income_ratio * bag_size/(.5*high_income_ratio))
    
    mask_size = 175
    base = './data/orthoimages/maskedblock/'
    img_fp = base + out_name + '.tif'
    print(f'{counter }: Bagging samples for {img_fp}')
    sample_bagging(img_fp, out_name, mask_size, bag_size=bag_size, black_thres = .10,
                   resize_ratio=.6, exclude_NIR=True, greyscale=True)
    counter += 1


0: Bagging samples for ./data/orthoimages/maskedblock/060750204012.tif
Resized area is [1005  595] pixels (from), (1675, 992)
Can sample ~19.525714285714287 unique images
Black ratio: 0.03131428571428571, writing to 060750204012_1.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.8614530612244898, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.40662857142857145, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.18553469387755103, skipping...
Black ratio: 0.4787265306122449, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0007183673469387755, writing to 060750204012_2.pkl
Black ratio: 0.0006204081632653061, writing to 060750204012_3.pkl
Black ratio: 0.8998204081632653, skipping...
Black ratio: 0.0950530612244898, writing to 060750204012_4.pkl
Black ratio: 

Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.9695020408163265, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.03800816326530612, writing to 060750204021_14.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.9447183673469388, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.25880816326530615, skipping...
Black ratio: 0.0003918367346938776, writing to 060750204021_15.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0, writing to 060750204021_16.pkl
Black ratio: 0.7888979591836734, skipping...
Black ra

Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.00013061224489795917, writing to 060750204022_17.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.00016326530612244898, writing to 060750204022_18.pkl
Black ratio: 0.5977795918367347, skipping...
Black ratio: 0.35278367346938777, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.4818612244897959, skipping...
Black ratio: 9.79591836734694e-05, writing to 060750204022_19.pkl
Black ratio: 3.265306122448979e-05, writing to 060750204022_20.pkl
Black ratio: 6.530612244897959e-05, writing to 060750204022_21.pkl
Black ratio: 0.00013061224489795917, writing to 060750204022_22.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.3222204081632653, skipping...
Black ratio: 0.3325061224489796, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 3.265306122448979e-05, writing to 060750204022_23.pkl
Bla

Resized area is [1507  932] pixels (from), (2512, 1553)
Can sample ~45.86200816326531 unique images
Black ratio: 0.22762448979591837, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.00035918367346938774, writing to 060750227042_1.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.00022857142857142857, writing to 060750227042_2.pkl
Black ratio: 0.0003918367346938776, writing to 060750227042_3.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.32303673469387756, skipping...
Black ratio: 0.00026122448979591835, writing to 060750227042_4.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.7540244897959184, skipping...
Black ratio: 0.11098775510204081, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0002938775510204082, writing to 060750227042_5.pkl
Black ratio: 0.1360326530612245, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0001959183673469388, writing to 060750227042_6.pkl
Black ratio: 0.000293877551020408

Black ratio: 1.0, skipping...
Black ratio: 0.1491265306122449, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.7780244897959183, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.04819591836734694, writing to 060750257011_18.pkl
Black ratio: 0.5133387755102041, skipping...
Black ratio: 0.00016326530612244898, writing to 060750257011_19.pkl
Black ratio: 0.3063836734693878, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0006857142857142857, writing to 060750257011_20.pkl
Black ratio: 0.9572897959183674, skipping...
Black ratio: 0.21871020408163266, skipping...
Black ratio: 0.2024816326530612, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.9617632653061224, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.39529795918367344, skipping...
Black ratio: 0.6678530612244898, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.970

...

Black ratio: 0.3833469387755102, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.0001959183673469388, writing to 060750228033_19.pkl
Black ratio: 0.9902693877551021, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.8434285714285714, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.6951510204081632, skipping...
Black ratio: 1.0, skipping...
Black ratio: 3.265306122448979e-05, writing to 060750228033_20.pkl
Black ratio: 0.9202938775510204, skipping...
Black ratio: 0.36558367346938775, skipping...
Black ratio: 0.00013061224489795917, writing to 060750228033_21.pkl
Black ratio: 0.38618775510204084, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.30589387755102043, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.47732244897959186, skipping...
Black ratio: 0.1724081632653061, skipping...
Black ratio: 0.004212244897959184, writing t

Black ratio: 1.0, skipping...
Black ratio: 0.005877551020408163, writing to 060750257022_14.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.5266938775510204, skipping...
Black ratio: 9.79591836734694e-05, writing to 060750257022_15.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.6039183673469388, skipping...
Black ratio: 6.530612244897959e-05, writing to 060750257022_16.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.40852244897959183, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.9731265306122449, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.9868734693877551, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.7900081632653061, sk

Black ratio: 0.0001959183673469388, writing to 060750478012_27.pkl
Black ratio: 0.00022857142857142857, writing to 060750478012_28.pkl
Black ratio: 9.79591836734694e-05, writing to 060750478012_29.pkl
Black ratio: 0.00026122448979591835, writing to 060750478012_30.pkl
Black ratio: 0.4439836734693878, skipping...
Black ratio: 9.79591836734694e-05, writing to 060750478012_31.pkl
Black ratio: 0.7456979591836734, skipping...
Black ratio: 0.00016326530612244898, writing to 060750478012_32.pkl
Black ratio: 0.6420571428571429, skipping...
Black ratio: 0.00035918367346938774, writing to 060750478012_33.pkl
Black ratio: 0.01113469387755102, writing to 060750478012_34.pkl
Black ratio: 0.6937795918367347, skipping...
Black ratio: 0.19578775510204083, skipping...
Black ratio: 0.00032653061224489796, writing to 060750478012_35.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.00013061224489795917, writing to 060750478012_36.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.8637387755102041, skipping.

Black ratio: 0.5699265306122449, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.26987755102040817, skipping...
Black ratio: 0.00016326530612244898, writing to 060750332032_18.pkl
Black ratio: 0.22857142857142856, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.30099591836734696, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.8807510204081632, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 3.265306122448979e-05, writing to 060750332032_19.pkl
Black ratio: 1.0, skipping...
Black ratio: 9.79591836734694e-05, writing to 060750332032_20.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.9996081632653061, skipping...
Black ratio: 0.1619591836734694, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.24777142857142856, skipping...
Black ratio: 0.

Black ratio: 0.7085714285714285, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.01616326530612245, writing to 060750119011_17.pkl
Black ratio: 0.0008489795918367347, writing to 060750119011_18.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.35921632653061225, skipping...
Black ratio: 0.0019918367346938777, writing to 060750119011_19.pkl
Black ratio: 1.0, skipping...
Black ratio: 1.0, skipping...
Black ratio: 0.17368163265306122, skipping...
Black ratio: 0.18122448979591838, skipping...
Black ratio: 0.2745795918367347, skipping...
Black ratio: 0.0005877551020408164, writing to 060750119011_20.pkl
Black ratio: 0.002416326530612245, writing to 060750119011_21.pkl
Black ratio: 0.0059755102040816325, writing to 060750119011_22.pkl
Black ratio: 0.002253061224489796, writing to 060750119011_23.pkl
Black ratio: 0.31640816326530613, skipping...
Black ratio: 0.07591836734693877, writing to 060750119011_24.pkl
Black ratio: 1.0, skipping...
Black ratio: 0.8896, skipping...
Black ratio: 